In [ ]:
%%writefile requirements.txt
gradio
tensorflow
numpy
pillow
opencv-python-headless


Overwriting requirements.txt


In [ ]:
!pip install gradio

In [ ]:
from google.colab import files

uploaded = files.upload()



Saving chest_xray_weights.h5 to chest_xray_weights.h5


In [ ]:
!ls

chest_xray_weights.h5  requirements.txt  sample_data


In [ ]:
%%writefile app.py
import gradio as gr
import tensorflow as tf
from tensorflow.keras.models import load_model
import numpy as np
from PIL import Image
import cv2
from tensorflow.keras.initializers import GlorotUniform
from tensorflow.keras.utils import custom_object_scope

# Load your trained model (upload your .h5 file to this directory or specify the path)
# Use a custom object scope to handle potential compatibility issues with GlorotUniform
with custom_object_scope({'GlorotUniform': GlorotUniform}):
    model = load_model('chest_xray_weights.h5')  # Replace with your actual filename


# Define your model's classes (update based on your training labels)
anatomy_classes = [
    "No Finding",
    "Atelectasis",
    "Cardiomegaly",
    "Consolidation",
    "Edema",
    "Effusion",
    "Emphysema",
    "Fibrosis",
    "Hernia",
    "Infiltration",
    "Mass",
    "Nodule",
    "Pneumonia",
    "Pneumothorax"
]

def predict_abnormality(image):
    try:
        # Preprocess the image (match your training setup)
        img = Image.fromarray(image).resize((224, 224))  # Adjust size to your model's input
        img_array = np.array(img)

        # Convert to grayscale if your model expects it
        if len(img_array.shape) == 3:
            img_array = cv2.cvtColor(img_array, cv2.COLOR_RGB2GRAY)

        img_array = img_array / 255.0  # Normalize
        img_array = np.expand_dims(img_array, axis=0)  # Add batch dimension
        img_array = np.expand_dims(img_array, axis=-1)  # Add channel if needed

        # Run prediction
        predictions = model.predict(img_array) # Removed [0] to inspect full output first
        predicted_index = np.argmax(predictions[0]) # Access the first prediction output
        confidence = predictions[0][predicted_index]

        # Format output
        if predicted_index == 0:  # Assuming index 0 is "Normal"
            return f"No abnormality detected. Confidence: {confidence:.2%}"
        else:
            issue = anatomy_classes[predicted_index]
            return f"Detected issue: {issue}. Confidence: {confidence:.2%}. Please consult a doctor."

    except Exception as e:
        print(f"Error details: {e}") # Print error details
        # Added print statements to help diagnose the error
        try:
            print(f"Shape of predictions: {predictions.shape}")
            print(f"Predictions: {predictions}")
            print(f"Predicted index: {predicted_index}")
            print(f"Number of anatomy classes: {len(anatomy_classes)}")

        except NameError:
            print("Predictions or predicted_index not defined before error.")

        return f"Error: {str(e)}. Try another image."

# Create the Gradio interface
demo = gr.Interface(
    fn=predict_abnormality,
    inputs=gr.Image(label="Upload Chest X-Ray Image", type="numpy"),
    outputs=gr.Textbox(label="Analysis Result"),
    title="Chest X-Ray Abnormality Detector",
    description="Upload an X-ray image to detect potential issues. For educational use only—not a medical diagnosis.",
    examples=[["sample_xray.jpg"]],  # Add paths to example images if available
    allow_flagging="never"
)

if __name__ == "__main__":
    demo.launch()


In [ ]:
import gradio as gr
import tensorflow as tf
from tensorflow.keras.models import load_model
import numpy as np
from PIL import Image
import cv2
from tensorflow.keras.initializers import GlorotUniform
from tensorflow.keras.utils import custom_object_scope

# Load your trained model (upload your .h5 file to this directory or specify the path)
# Use a custom object scope to handle potential compatibility issues with GlorotUniform
with custom_object_scope({'GlorotUniform': GlorotUniform}):
    model = load_model('chest_xray_weights.h5')  # Replace with your actual filename


# Define your model's classes (update based on your training labels)
anatomy_classes = [
    "No Finding",
    "Atelectasis",
    "Cardiomegaly",
    "Consolidation",
    "Edema",
    "Effusion",
    "Emphysema",
    "Fibrosis",
    "Hernia",
    "Infiltration",
    "Mass",
    "Nodule",
    "Pneumonia",
    "Pneumothorax"
]

def predict_abnormality(image):
    try:
        # Preprocess the image (match your training setup)
        img = Image.fromarray(image).resize((224, 224))  # Adjust size to your model's input
        img_array = np.array(img)

        # Convert to grayscale if your model expects it
        if len(img_array.shape) == 3:
            img_array = cv2.cvtColor(img_array, cv2.COLOR_RGB2GRAY)

        img_array = img_array / 255.0  # Normalize
        img_array = np.expand_dims(img_array, axis=0)  # Add batch dimension
        img_array = np.expand_dims(img_array, axis=-1)  # Add channel if needed

        # Run prediction
        predictions = model.predict(img_array) # Removed [0] to inspect full output first
        predicted_index = np.argmax(predictions[0]) # Access the first prediction output
        confidence = predictions[0][predicted_index]

        # Format output
        if predicted_index == 0:  # Assuming index 0 is "Normal"
            return f"No abnormality detected. Confidence: {confidence:.2%}"
        else:
            issue = anatomy_classes[predicted_index]
            return f"Detected issue: {issue}. Confidence: {confidence:.2%}. Please consult a doctor."

    except Exception as e:
        print(f"Error details: {e}") # Print error details
        # Added print statements to help diagnose the error
        try:
            print(f"Shape of predictions: {predictions.shape}")
            print(f"Predictions: {predictions}")
            print(f"Predicted index: {predicted_index}")
            print(f"Number of anatomy classes: {len(anatomy_classes)}")

        except NameError:
            print("Predictions or predicted_index not defined before error.")

        return f"Error: {str(e)}. Try another image."

# Create the Gradio interface
demo = gr.Interface(
    fn=predict_abnormality,
    inputs=gr.Image(label="Upload Chest X-Ray Image", type="numpy"),
    outputs=gr.Textbox(label="Analysis Result"),
    title="Chest X-Ray Abnormality Detector",
    description="Upload an X-ray image to detect potential issues. For educational use only—not a medical diagnosis.",
    examples=[["sample_xray.jpg"]],  # Add paths to example images if available
    allow_flagging="never"
)

if __name__ == "__main__":
    demo.launch()

/usr/local/lib/python3.11/dist-packages/gradio/interface.py:416: UserWarning: The `allow_flagging` parameter in `Interface` is deprecated.Use `flagging_mode` instead.
  warnings.warn(


It looks like you are running Gradio on a hosted a Jupyter notebook. For the Gradio app to work, sharing must be enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. To show errors in colab notebook, set debug=True in launch()
* Running on public URL: https://0b58124b323893b4d0.gradio.live

This share link expires in 1 week. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


In [ ]:
from google.colab import drive
drive.mount('/content/drive')

In [ ]:
!gradio deploy

Creating new Spaces Repo in '/content'. Collecting metadata, press Enter to 
accept default value.
Enter Spaces app title [content]: 

In [ ]:
!pip install h5py tensorflow


In [ ]:
# Script: Upload and Handle .h5 File in Colab

# Step 1: Import necessary libraries
from google.colab import files
from tensorflow.keras.models import load_model
import h5py
import os

# Step 2: Upload the .h5 file
print("Please upload your .h5 file:")
uploaded = files.upload()

# Step 3: Get the uploaded filename (assumes single file upload)
filename = list(uploaded.keys())[0]  # e.g., 'chest_xray_model.h5'
print(f"Uploaded file: {filename}")

# Step 4: Verify file existence and size
if os.path.exists(filename):
    file_size = os.path.getsize(filename) / (1024 * 1024)  # Size in MB
    print(f"File size: {file_size:.2f} MB")
else:
    print("Upload failed. Please try again.")
    raise SystemExit

# Step 5: Handle as HDF5 file (general inspection)
with h5py.File(filename, 'r') as f:
    print("HDF5 keys:", list(f.keys()))

# Step 6: Load as Keras model (if it's a model file)
try:
    model = load_model(filename)
    print("Model loaded successfully!")
    model.summary()  # Print model architecture
except Exception as e:
    print(f"Error loading as Keras model: {e}")

# Optional: Save or process further
# model.save('processed_model.h5')  # Example: Resave if modified


Please upload your .h5 file:


In [ ]:
# Uninstall current TensorFlow version
!pip uninstall tensorflow -y

# Install TensorFlow 2.8
!pip install tensorflow==2.8

# After running this cell, restart the Colab runtime (Runtime -> Restart runtime)
# Then, re-run the cell containing your model loading and Gradio interface code (cell ID ABo9ZTOIROmK)

Found existing installation: tensorflow 2.18.0
Uninstalling tensorflow-2.18.0:
  Successfully uninstalled tensorflow-2.18.0
ERROR: Could not find a version that satisfies the requirement tensorflow==2.8 (from versions: 2.12.0rc0, 2.12.0rc1, 2.12.0, 2.12.1, 2.13.0rc0, 2.13.0rc1, 2.13.0rc2, 2.13.0, 2.13.1, 2.14.0rc0, 2.14.0rc1, 2.14.0, 2.14.1, 2.15.0rc0, 2.15.0rc1, 2.15.0, 2.15.0.post1, 2.15.1, 2.16.0rc0, 2.16.1, 2.16.2, 2.17.0rc0, 2.17.0rc1, 2.17.0, 2.17.1, 2.18.0rc0, 2.18.0rc1, 2.18.0rc2, 2.18.0, 2.18.1, 2.19.0rc0, 2.19.0)
ERROR: No matching distribution found for tensorflow==2.8


In [ ]:
model.summary()

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 conv2d (Conv2D)             (None, 222, 222, 32)      320       
                                                                 
 max_pooling2d (MaxPooling2D  (None, 111, 111, 32)     0         
 )                                                               
                                                                 
 conv2d_1 (Conv2D)           (None, 109, 109, 64)      18496     
                                                                 
 max_pooling2d_1 (MaxPooling  (None, 54, 54, 64)       0         
 2D)                                                             
                                                                 
 conv2d_2 (Conv2D)           (None, 52, 52, 128)       73856     
                                                                 
 max_pooling2d_2 (MaxPooling  (None, 26, 26, 128)      0